# Mean Teacher Bert Assessment



# Requirement Installation 

In [2]:
#installing requirements
!pip install tensorflow_text
!pip install textattack #==0.3.0
!pip install sentence_transformers

     |████████████████████████████████| 4.9 MB 5.2 MB/s 
     |████████████████████████████████| 373 kB 5.2 MB/s 
     |████████████████████████████████| 769 kB 49.1 MB/s 
     |████████████████████████████████| 59 kB 6.8 MB/s 
     |████████████████████████████████| 3.1 MB 46.3 MB/s 
     |████████████████████████████████| 101 kB 10.8 MB/s 
     |████████████████████████████████| 322 kB 59.3 MB/s 
     |████████████████████████████████| 69 kB 7.3 MB/s 
     |████████████████████████████████| 298 kB 47.5 MB/s 
     |████████████████████████████████| 59 kB 6.5 MB/s 
     |████████████████████████████████| 596 kB 62.1 MB/s 
     |████████████████████████████████| 895 kB 40.7 MB/s 
     |████████████████████████████████| 3.3 MB 35.5 MB/s 
     |████████████████████████████████| 132 kB 59.4 MB/s 
     |████████████████████████████████| 298 kB 65.1 MB/s 
     |████████████████████████████████| 290 kB 53.7 MB/s 
     |████████████████████████████████| 290 kB 52.6 MB/s 
     |████████████████


# Importing and Declaration

In [3]:
import os 
os.chdir('/content/drive/MyDrive/Master Thesis/Mean-Teacher-BERT-Robustness-Assessment/')

In [4]:
# importing libraries 
import os 
import datetime

import pandas as pd 
import numpy as np
import tensorflow as tf

from ipywidgets import *
from IPython.display import display


from Utils.utils import label_to_int, dataset_split, convert_to_category, create_tokenizer, data_tokenization
from Utils.data_loader import data_loader
from Bert.bert_model import bert_model



from MeanTeacher.train_mean_teacher import train_mean_teacher

from sklearn.metrics import classification_report

import random 
random.seed(42)

## Data Related Questionaire

In [5]:
data_name=widgets.Dropdown(options=['codalab','IMDB' ],value='IMDB',description='DATA:',disabled=False,) 
pretrained_weights=widgets.Dropdown(options=['bert-base-uncased','distilbert-base-uncased' ],value='distilbert-base-uncased',description='Pretrained Model:',disabled=False,)
widgets.HBox([data_name, pretrained_weights])

### Data specific detail

In [6]:
'''
NOT required now as previous cell does the job. So disabling boxes
'''
# Details related to the dataset
# columns names 
feature_col=widgets.Text(value='tweet',placeholder='Enter Feature Col Name',description='Feature Column:',disabled=False)
target_col=widgets.Text(value='label',placeholder='Enter Target Col Name',description='Target Column:',disabled=False) 
aug_col=widgets.Text(value='aug_tweet',placeholder='Enter Augmented data Col Name',description='Augment Column:',disabled=False)   

#pretrained model details
 # widgets.HBox([feature_col,target_col,aug_col,pretrained_weights])

In [7]:
#details of the class
class_1=widgets.Text(value='real',placeholder='Enter class name 1',description='class 1:',disabled=False)
class_2=widgets.Text(value='fake',placeholder='Enter class name 2',description='class 2:',disabled=False) 
tf.print("Class 1 label would be 0. \n")
# widgets.HBox([class_1,class_2])

Class 1 label would be 0. 



In [8]:
# #Data location 
Data_loc=widgets.Text(value='Data/codalab/',placeholder='Enter Data location ',description=' Data Location Column:',disabled=False)   
# widgets.HBox([Data_loc])

In [9]:
'''
Adjusting feature as per data 
'''

if data_name.value=='codalab':
    feature_col.value='tweet'
    target_col.value='label'
    aug_col.value='aug_tweet'
    class_1.value='real'
    class_2.value='fake'
    Data_loc.value= 'Data/codalab/'
elif data_name.value=='IMDB':
    feature_col.value='review'
    target_col.value='sentiment'
    aug_col.value='aug_tweet'
    class_1.value='positive'
    class_2.value='negative'
    Data_loc.value= 'Data/IMDB/'



## Hyperparameter selections

In [10]:
# Parameter declaration 
max_len=widgets.BoundedIntText(value=100,min=10,max=512,step=10,description='Max Length:',disabled=False,)

learning_rate= widgets.Dropdown(options=[2e-5, 1e-5, 1e-3],value=2e-5,description='Learning Rate:',disabled=False,)

epochs= widgets.Dropdown(options=[3, 4, 5,6],value=3,description='Epochs:',disabled=False,)

batch_size= widgets.Dropdown(options=[4, 5,6,7,8],value=4,description='Batch Size:',disabled=False,)

#for mean teacher model
alpha= widgets.BoundedFloatText(value=0.999,min=0.90,max=0.999,step=0.0001,description='Alpha:',disabled=False, readout_format='.3f')
ratio= widgets.BoundedFloatText(value=0.5,min=0.1,max=0.9,step=0.1,description='Ratio:',disabled=False, readout_format='.2f')
# pretrained_weights=widgets.Dropdown(options=['bert-base-uncased','distilbert-base-uncased' ],value='bert-base-uncased',description='Pretrained Model:',disabled=False,)

tf.print('\n Max Length: Length of the article')
display(max_len)
tf.print('\n Learning rate: Learning rate for training the model')
display(learning_rate)
tf.print('\n Epochs')
display(epochs)
tf.print('\n batch_size')
display(batch_size)
tf.print('\n Alpha: Parameter related to Mean teacher model, its the proportion of student weight that teacher model will get each step.')
display(alpha)
tf.print("\n Ratio: Parameter related to Mean Teacher model, that manage the proportion of classification cost and consistency cost in calculating overall cost.")
display(ratio)

# widgets.HBox([max_len, learning_rate, epochs, batch_size,alpha,ratio])


 Max Length: Length of the article


BoundedIntText(value=100, description='Max Length:', max=512, min=10, step=10)


 Learning rate: Learning rate for training the model


Dropdown(description='Learning Rate:', options=(2e-05, 1e-05, 0.001), value=2e-05)


 Epochs


...

Dropdown(description='Batch Size:', options=(4, 5, 6, 7, 8), value=4)


 Alpha: Parameter related to Mean teacher model, its the proportion of student weight that teacher model will get each step.


BoundedFloatText(value=0.999, description='Alpha:', max=0.999, min=0.9, step=0.0001)


 Ratio: Parameter related to Mean Teacher model, that manage the proportion of classification cost and consistency cost in calculating overall cost.


BoundedFloatText(value=0.5, description='Ratio:', max=0.9, min=0.1, step=0.1)

# Reading dataset

In [11]:
df_train,df_test,df_aug_unlabel= data_loader(Data_loc.value,target_col.value,aug_col.value,class_1.value)

In [12]:
len(df_train),len(df_test)

(6050, 2000)

In [13]:
tf.print(df_train.groupby(target_col.value).count())
tf.print(df_test.groupby(target_col.value).count())

           review
sentiment        
0            3025
1            3025
           review
sentiment        
0            1000
1            1000


# Training 

<font color='blue'>This section is to train and save the model. <br>
__If model is already trained and saved, directly move forward for attack and evaluation section.__ </font>

## BERT Model Training

In [14]:
pretrained_weights.value

'distilbert-base-uncased'

In [15]:
tokenizer=create_tokenizer(pretrained_weights.value)
x_train,y_train,vocab_size= data_tokenization(df_train,feature_col.value,target_col.value,max_len.value,tokenizer)
x_test,y_test,_= data_tokenization(df_test,feature_col.value,target_col.value,max_len.value,tokenizer)

In [16]:
#printing hyperparameters set for training 
print(f'Alpha: {alpha.value}, Max len : {max_len.value}, Learning Rate: {learning_rate.value}, Batch Size: {batch_size.value}, Ratio: {ratio.value}, Epochs: {epochs.value}')

Alpha: 0.999, Max len : 100, Learning Rate: 2e-05, Batch Size: 4, Ratio: 0.5, Epochs: 3


In [17]:
bert=bert_model(pretrained_weights.value,max_len.value,learning_rate.value)
bert.summary()

Model selected: distilbert-base-uncased


Some layers from the model checkpoint at distilbert-base-uncased were not used when initializing TFDistilBertModel: ['vocab_layer_norm', 'vocab_transform', 'vocab_projector', 'activation_13']
- This IS expected if you are initializing TFDistilBertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing TFDistilBertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
All the layers of TFDistilBertModel were initialized from the model checkpoint at distilbert-base-uncased.
If your task is similar to the task the model of the checkpoint was trained on, you can already use TFDistilBertModel for predictions without further training.


Model: "model"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 input_ids (InputLayer)         [(None, 100)]        0           []                               
                                                                                                  
 attention_mask (InputLayer)    [(None, 100)]        0           []                               
                                                                                                  
 tf_distil_bert_model (TFDistil  TFBaseModelOutput(l  66362880   ['input_ids[0][0]',              
 BertModel)                     ast_hidden_state=(N               'attention_mask[0][0]']         
                                one, 100, 768),                                                   
                                 hidden_states=None                                           

In [18]:
print(datetime.datetime.now())
with tf.device('/GPU:0'):
    bert.fit(x_train,y_train,batch_size=batch_size.value,epochs=epochs.value,verbose=1)

2021-11-27 10:53:40.537232
Epoch 1/3


KeyboardInterrupt: ignored

In [ ]:
# evaluating model 
pred_label=bert.predict(x_test)

print(classification_report(np.argmax(y_test,1),np.argmax(pred_label,1)))

In [ ]:
#saving the model 
if  pretrained_weights.value == 'distilbert-base-uncased':
    bert.save_weights('SavedModels/'+data_name.value+'/DistilBERT_model.h5')
else:
    bert.save_weights('SavedModels/'+data_name.value+'/BERT_model.h5')

## Adversarial Mean Teacher BERT Training

In [ ]:
# Training
tokenizer=create_tokenizer(pretrained_weights.value)
x_train,y_train,vocab_size= data_tokenization(df_train,feature_col.value,target_col.value,max_len.value,tokenizer)
x_test,y_test,_= data_tokenization(df_test,feature_col.value,target_col.value,max_len.value,tokenizer)
x_unlabel,_,_=data_tokenization(df_aug_unlabel,aug_col.value,target_col.value,max_len.value,tokenizer)

In [ ]:
#printing hyperparameters set for training 
print(f'Alpha: {alpha.value}, Max len : {max_len.value}, Learning Rate: {learning_rate.value}, Batch Size: {batch_size.value}, Ratio: {ratio.value}, Epochs: {epochs.value}')


In [ ]:
print(datetime.datetime.now())
# training the model
with tf.device('/GPU:0'):
    student, teacher= train_mean_teacher(x_train, y_train, x_unlabel, 
                                         pretrained_weights.value,
                                         epochs.value,batch_size.value,
                                         learning_rate.value,max_len.value,alpha.value)

In [ ]:
if  pretrained_weights.value == 'distilbert-base-uncased':
    teacher.save_weights('SavedModels/'+data_name.value+'/DistilBERT_teacher.h5')
else:
    teacher.save_weights('SavedModels/'+data_name.value+'/BERT_teacher.h5')


In [ ]:
#evaluating test data 
pred_label=teacher.predict(x_test)

In [ ]:
print(classification_report(np.argmax(y_test,1),np.argmax(pred_label,1)))

# Attack And Evaluation

In [19]:
import textattack
from Attack_model.TextAttack import attack_model

textattack: Updating TextAttack package dependencies.
textattack: Downloading NLTK required packages.


[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /root/nltk_data...
[nltk_data]   Unzipping taggers/averaged_perceptron_tagger.zip.
[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.
[nltk_data] Downloading package omw to /root/nltk_data...
[nltk_data]   Unzipping corpora/omw.zip.
[nltk_data] Downloading package universal_tagset to /root/nltk_data...
[nltk_data]   Unzipping taggers/universal_tagset.zip.
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Unzipping corpora/wordnet.zip.
[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.


textattack: Downloading https://textattack.s3.amazonaws.com/word_embeddings/paragramcf.
100%|██████████| 481M/481M [00:11<00:00, 41.7MB/s]
textattack: Unzipping file /root/.cache/textattack/tmp7ds7sbom.zip to /root/.cache/textattack/word_embeddings/paragramcf.
textattack: Successfully saved word_embeddings/paragramcf to cache.


In [20]:
# bert_to_attack=widgets.Textarea(value='SavedModels/Codalab/BERT_model.h5',placeholder='Enter Model location ',description=' BERT Model location:',disabled=False)
# MTbert_to_attack=widgets.Textarea(value='SavedModels/Codalab/BERT_teacher.h5',placeholder='Enter Model location ',description=' MTBERT Model location:',disabled=False)   
# pretrained_weights=widgets.Dropdown(options=['bert-base-uncased','distilbert-base-uncased' ],value='bert-base-uncased',description='Pretrained Model:',disabled=False,) 
model_name=widgets.Dropdown(options=['BERT','DistilBERT']
                               ,value='DistilBERT',
                               description='Model Name:',
                               disabled=False,) 
tf.print('\n model_name: Model name for attack.Note : Please confirm with the bert_to_attack parameter')
display(model_name)

# tf.print('\n Please select the location of BERT and MT BERT model.\n')
# display(bert_to_attack, MTbert_to_attack)
# tf.print('\n Please select the pretrained model weights.')
# display(pretrained_weights)



 model_name: Model name for attack.Note : Please confirm with the bert_to_attack parameter


Dropdown(description='Model Name:', index=1, options=('BERT', 'DistilBERT'), value='DistilBERT')

In [21]:
if model_name.value=='BERT':
  bert_to_attack= 'SavedModels/'+data_name.value+'/BERT_model.h5'
  MTbert_to_attack='SavedModels/'+data_name.value+'/BERT_teacher.h5'
  pretrained_weights.value = 'bert-base-uncased'
else:
  bert_to_attack= 'SavedModels/'+data_name.value+'/DistilBERT_model.h5'
  MTbert_to_attack='SavedModels/'+data_name.value+'/DistilBERT_teacher.h5'
  pretrained_weights.value = 'distilbert-base-uncased'
print(model_name.value), bert_to_attack

DistilBERT


(None, 'SavedModels/IMDB/DistilBERT_model.h5')

In [22]:
# attack parameters 

# Query Budget is maximum query allowed
query_budget= widgets.BoundedIntText(value=1000,min=10,max=2000,step=20,description='Query Budget:',disabled=False,)

# number of example to take for attack from test dataset randomly 
num_examples=widgets.BoundedIntText(value=1000,min=10,max=len(df_test),step=20,description='Number of Example:',disabled=False,)

# attack recipes 
attack_recipe=widgets.Dropdown(options=['TextFoolerJin2019',
                                        'PWWSRen2019',
                                        'BERTAttackLi2020',
                                        'BAEGarg2019',
                                        'TextBuggerLi2018',
                                        'CLARE2020',
                                        'MorpheusTan2020',
                                        'A2TYoo2021',
                                        'PSOZang2020']
                               ,value='TextFoolerJin2019',
                               description='Attack Recipe:',
                               disabled=False,) 


tf.print('\n query_budget: Maximum Query allowed to attack model')
display(query_budget)
tf.print('\n num_examples: Number of example to take for attack from test dataset randomly. ')
display(num_examples)
# tf.print('\n attack_recipe: Attack methodolgy to attack the model. ')
# display(attack_recipe)



 query_budget: Maximum Query allowed to attack model


BoundedIntText(value=1000, description='Query Budget:', max=2000, min=10, step=20)


 num_examples: Number of example to take for attack from test dataset randomly. 


BoundedIntText(value=1000, description='Number of Example:', max=2000, min=10, step=20)

In [23]:
'''
Some of the attack recipe provided by textattack is not working with lengthy article. So, 
I am filtering the with the length. May be in future I will remove it.
'''
if not os.path.exists('Data/'+data_name.value+'/AdversarialTestData/test_adv_'+str(num_examples.value)+'.csv'):
    df_test['len']=df_test.apply(lambda row: len(row[feature_col.value].split()),axis=1)
    print(f'Average length of articles are: {df_test["len"].mean()}')
    # df_test_for_attack= df_test[(df_test['len']>0) & (df_test['len']<100)][[feature_col.value,target_col.value]].dropna().reset_index(drop=True)
    df_test_for_attack=df_test[[feature_col.value,target_col.value]].sample(frac=1).reset_index(drop=True)
    df_test_for_attack= df_test_for_attack[:num_examples.value+1]
    # saving the csv file in AdversarialTestData folder, in order to correctly experiment all recipes with same data
    df_test_for_attack.to_csv('Data/'+data_name.value+'/AdversarialTestData/test_adv_'+str(num_examples.value)+'.csv',index=False)
else:
    tf.print('Reading the saved file')
    df_test_for_attack= pd.read_csv('Data/'+data_name.value+'/AdversarialTestData/test_adv_'+str(num_examples.value)+'.csv')

print('Length of dataset', len(df_test_for_attack))
df_test_for_attack.head()

Reading the saved file
Length of dataset 1001


review  sentiment
0  this is perhaps the creepiest display of santa...          1
1  it was a good story  but not very well told  i...          1
2  this film  although not totally bad  should ha...          1
3  the film is set in newcastle on tyne in north ...          1
4  a very bad attempt at a young spinal tap  at l...          1

In [24]:
df_test_for_attack.groupby(target_col.value).count()

review
sentiment        
0             502
1             499

In [25]:

#creating dataset for the attacking
dataset_for_attack=list(df_test_for_attack.itertuples(index=False, name=None))
dataset_for_attack = textattack.datasets.Dataset(dataset_for_attack)

In [26]:
# Loading the model
bert= bert_model(pretrained_weights.value,max_len.value,learning_rate.value) 
bert.load_weights(bert_to_attack)

bert_teacher= bert_model(pretrained_weights.value,max_len.value,learning_rate.value) 
bert_teacher.load_weights(MTbert_to_attack)

Model selected: distilbert-base-uncased


Some layers from the model checkpoint at distilbert-base-uncased were not used when initializing TFDistilBertModel: ['vocab_layer_norm', 'vocab_transform', 'vocab_projector', 'activation_13']
- This IS expected if you are initializing TFDistilBertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing TFDistilBertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
All the layers of TFDistilBertModel were initialized from the model checkpoint at distilbert-base-uncased.
If your task is similar to the task the model of the checkpoint was trained on, you can already use TFDistilBertModel for predictions without further training.


Model selected: distilbert-base-uncased


Some layers from the model checkpoint at distilbert-base-uncased were not used when initializing TFDistilBertModel: ['vocab_layer_norm', 'vocab_transform', 'vocab_projector', 'activation_13']
- This IS expected if you are initializing TFDistilBertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing TFDistilBertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
All the layers of TFDistilBertModel were initialized from the model checkpoint at distilbert-base-uncased.
If your task is similar to the task the model of the checkpoint was trained on, you can already use TFDistilBertModel for predictions without further training.


### TextFooler
__TextFoolerJin2019 - Is BERT Really Robust? A Strong Baseline for Natural Language Attack on Text Classification and Entailment.__<br>
In this paper, we present TextFooler, a simple but strong baseline to generate natural adversarial text. By applying it to two fundamental natural language tasks, text classification and textual entailment, we successfully attacked three target models, including the powerful pre-trained BERT, and the widely used convolutional and recurrent neural networks. We demonstrate the advantages of this framework in three ways: (1) effective---it outperforms state-of-the-art attacks in terms of success rate and perturbation rate, (2) utility-preserving---it preserves semantic content and grammaticality, and remains correctly classified by humans, and (3) efficient---it generates adversarial text with computational complexity linear to the text length. *The code, pre-trained target models, and test examples are available at https://github.com/jind11/TextFooler.


In [ ]:
attack_recipe.value= 'TextFoolerJin2019'
tf.print(f'****Attack Recipe:{attack_recipe.value}*****')
tf.print(f'****Query size:{query_budget.value}*****')
tf.print(f'****Number of examples:{num_examples.value}*****')
tf.print(f'****Attacking model :{model_name.value}*****')

****Attack Recipe:TextFoolerJin2019*****
****Query size:1000*****
****Number of examples:1000*****
****Attacking model :DistilBERT*****


#### BERT

In [ ]:
attack_model(bert, 
             dataset_for_attack,
             data_name.value,
             pretrained_weights.value,
             max_len.value,
             model_name.value,
             attack_recipe=attack_recipe.value,
             query_budget= query_budget.value,
             num_examples=num_examples.value)

textattack: Unknown if model of class <class 'keras.engine.functional.Functional'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path Result/IMDB/TextFoolerJin2019/DistilBERT_nexp1000_qb1000_2021-11-27_07:33.csv

  0%|          | 0/1000 [00:00<?, ?it/s]

Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.840845057
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']
       


  0%|          | 1/1000 [00:13<3:39:53, 13.21s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   0%|          | 1/1000 [00:13<3:40:20, 13.23s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   0%|          | 2/1000 [00:13<1:51:11,  6.69s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 1 / 2:   0%|          | 2/1000 [00:13<1:51:24,  6.70s/it]

--------------------------------------------- Result 1 ---------------------------------------------
[[1 (73%)]] --> [[0 (51%)]]

this is perhaps the [[creepiest]] display of [[santa]] claus ever [[committed]] to any medium  whether it be a book  a [[picture]]  or a movie  santa looks [[like]] a [[perv]] [[looking]] down on the [[children]] and the twisted [[story]] of inging merlin in to help him defeat one of [[satan]] s minions  [[pitch]]  doesn t [[make]] [[things]] any [[better]]  it s laughable to [[say]] the least  with [[bad]] [[effects]]  even for   standards  if a [[kid]] were to [[watch]] this [[movie]]  he d have nightmares and never want santa to visit  they d be scarred for life  imagine the kid s in  a christmas story  when they start screaming after being put on santa s lap  that s how this would turn out if kid s see this movie 

this is perhaps the [[strangest]] display of [[christmastime]] claus ever [[launched]] to any medium  whether it be a book  a [[landscapes]] 


[Succeeded / Failed / Skipped / Total] 1 / 0 / 1 / 2:   0%|          | 3/1000 [00:16<1:28:49,  5.35s/it]
[Succeeded / Failed / Skipped / Total] 2 / 0 / 1 / 3:   0%|          | 3/1000 [00:16<1:28:57,  5.35s/it]

...

--------------------------------------------- Result 998 ---------------------------------------------
[[1 (73%)]] --> [[0 (61%)]]

i saw this film because calexico did the score  a [[real]] disappointment  [[annoying]]  trendy scenes  with urban hipsters and their cliche hip lifestyles  cheesy stereotypical mexican border culture  mystic grandfather with the rattlesnake and potions  granddaughter in her mariachi style restaurant getup  a few laughs  but hipper than thou  and sorely [[lacking]] in vision and basic filmmaking talent 

i saw this film because calexico did the score  a [[truths]] disappointment  [[unnerving]]  trendy scenes  with urban hipsters and their cliche hip lifestyles  cheesy stereotypical mexican border culture  mystic grandfather with the rattlesnake and potions  granddaughter in her mariachi style restaurant getup  a few laughs  but hipper than thou  and sorely [[rarity]] in vision and basic filmmaking talent 





[Succeeded / Failed / Skipped / Total] 904 / 26 / 68 / 998: 100%|█████████▉| 999/1000 [46:43<00:02,  2.81s/it]
[Succeeded / Failed / Skipped / Total] 905 / 26 / 68 / 999: 100%|█████████▉| 999/1000 [46:43<00:02,  2.81s/it]

--------------------------------------------- Result 999 ---------------------------------------------
[[1 (72%)]] --> [[0 (51%)]]

 spoilers ahead  this same exact plot from this movie has been done before  it has been done in ferris bueller s day off  marques  bat man  houston plays [[sick]]  his [[gullible]] parents believe him  his sister knows that he s faking  but she still must go to school  she is mad  he has a party with his friends while his parents are away  by the time his parents get home  he is sick again and his parents never found out about the party  i like [[immature]] better when they were in house party   and still immature 

 spoilers ahead  this same exact plot from this movie has been done before  it has been done in ferris bueller s day off  marques  bat man  houston plays [[queasy]]  his [[ingenuous]] parents believe him  his sister knows that he s faking  but she still must go to school  she is mad  he has a party with his friends while his parents are away  b


[Succeeded / Failed / Skipped / Total] 905 / 26 / 68 / 999: 100%|██████████| 1000/1000 [46:46<00:00,  2.81s/it]
[Succeeded / Failed / Skipped / Total] 906 / 26 / 68 / 1000: 100%|██████████| 1000/1000 [46:46<00:00,  2.81s/it]


--------------------------------------------- Result 1000 ---------------------------------------------
[[1 (73%)]] --> [[0 (50%)]]

from reading the back of the box my first thought was that this is probably a [[knock]] off of saw    i couldn t be further from the [[truth]]  it seemed to me [[like]] they gave somebody with downsyndrom a camera phone and      and told them to make a movie  the plot didn t exist and neither did the acting  it was almost as if i was watching a silent film about [[grass]] [[growing]]  it didn t surprise me at all to find out later that the entire film was  improvised  by the end of this  film  i had lost the will to live and i may have gotten aids just from viewing this piece of cinematic crap  it was about   minutes that i could have spent doing something that was less painful  like jumping off of a building 

from reading the back of the box my first thought was that this is probably a [[jolts]] off of saw    i couldn t be further from the [[truthful]] 

#### MT BERT

In [ ]:
attack_model(bert_teacher, 
             dataset_for_attack,
             data_name.value,
             pretrained_weights.value,
             max_len.value,
             'MT'+model_name.value,
             attack_recipe=attack_recipe.value,
             query_budget= query_budget.value,
             num_examples=num_examples.value)

textattack: Unknown if model of class <class 'keras.engine.functional.Functional'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path Result/IMDB/TextFoolerJin2019/MTDistilBERT_nexp1000_qb1000_2021-11-27_08:19.csv

  0%|          | 0/1000 [00:00<?, ?it/s]

Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.840845057
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']
       


  0%|          | 1/1000 [00:16<4:35:48, 16.57s/it]
[Succeeded / Failed / Skipped / Total] 0 / 1 / 0 / 1:   0%|          | 1/1000 [00:16<4:36:17, 16.59s/it]

--------------------------------------------- Result 1 ---------------------------------------------
[[1 (63%)]] --> [[[FAILED]]]

this is perhaps the creepiest display of santa claus ever committed to any medium  whether it be a book  a picture  or a movie  santa looks like a perv looking down on the children and the twisted story of inging merlin in to help him defeat one of satan s minions  pitch  doesn t make things any better  it s laughable to say the least  with bad effects  even for   standards  if a kid were to watch this movie  he d have nightmares and never want santa to visit  they d be scarred for life  imagine the kid s in  a christmas story  when they start screaming after being put on santa s lap  that s how this would turn out if kid s see this movie 





[Succeeded / Failed / Skipped / Total] 0 / 1 / 0 / 1:   0%|          | 2/1000 [00:26<3:37:11, 13.06s/it]
[Succeeded / Failed / Skipped / Total] 1 / 1 / 0 / 2:   0%|          | 2/1000 [00:26<3:37:23, 13.07s/it]

...

--------------------------------------------- Result 998 ---------------------------------------------
[[1 (65%)]] --> [[0 (50%)]]

i [[saw]] this film because calexico did the score  a real [[disappointment]]  annoying  trendy scenes  with [[urban]] hipsters and their cliche [[hip]] [[lifestyles]]  [[cheesy]] [[stereotypical]] mexican border [[culture]]  mystic [[grandfather]] with the [[rattlesnake]] and [[potions]]  granddaughter in her mariachi [[style]] restaurant [[getup]]  a [[few]] [[laughs]]  but hipper than thou  and sorely lacking in vision and [[basic]] filmmaking [[talent]] 

i [[enjoyed]] this film because calexico did the score  a real [[consternation]]  annoying  trendy scenes  with [[stadt]] hipsters and their cliche [[peep]] [[iife]]  [[cutesy]] [[stereotype]] mexican border [[cultivate]]  mystic [[pere]] with the [[rattlesnakes]] and [[tonics]]  granddaughter in her mariachi [[manner]] restaurant [[standup]]  a [[rare]] [[jokes]]  but hipper than thou  and sorely lac


[Succeeded / Failed / Skipped / Total] 630 / 297 / 71 / 998: 100%|█████████▉| 999/1000 [1:30:48<00:05,  5.45s/it]
[Succeeded / Failed / Skipped / Total] 631 / 297 / 71 / 999: 100%|█████████▉| 999/1000 [1:30:48<00:05,  5.45s/it]

--------------------------------------------- Result 999 ---------------------------------------------
[[1 (62%)]] --> [[0 (50%)]]

 spoilers ahead  this same exact [[plot]] from this movie has been done before  it has been done in ferris bueller s day off  marques  bat man  houston plays sick  his gullible parents believe him  his sister knows that he s faking  but she still must go to school  she is mad  he has a party with his friends while his parents are away  by the time his parents get home  he is sick again and his parents never found out about the party  i like immature better when they were in house party   and still immature 

 spoilers ahead  this same exact [[tracts]] from this movie has been done before  it has been done in ferris bueller s day off  marques  bat man  houston plays sick  his gullible parents believe him  his sister knows that he s faking  but she still must go to school  she is mad  he has a party with his friends while his parents are away  by the time hi


[Succeeded / Failed / Skipped / Total] 631 / 297 / 71 / 999: 100%|██████████| 1000/1000 [1:30:54<00:00,  5.45s/it]
[Succeeded / Failed / Skipped / Total] 632 / 297 / 71 / 1000: 100%|██████████| 1000/1000 [1:30:54<00:00,  5.45s/it]

--------------------------------------------- Result 1000 ---------------------------------------------
[[1 (66%)]] --> [[0 (50%)]]

from reading the back of the box my first thought was that this is probably a [[knock]] off of [[saw]]    i couldn t be [[further]] from the [[truth]]  it seemed to me [[like]] they gave [[somebody]] with downsyndrom a camera phone and      and told them to make a movie  the [[plot]] didn t [[exist]] and neither did the acting  it was almost as if i was watching a silent film about grass [[growing]]  it didn t [[surprise]] me at all to find out [[later]] that the entire [[film]] was  improvised  by the [[end]] of this  film  i had lost the will to live and i may have gotten aids just from viewing this piece of cinematic crap  it was about   minutes that i could have spent doing something that was less painful  like jumping off of a building 

from reading the back of the box my first thought was that this is probably a [[jolted]] off of [[seen]]    i coul

### TextBugger
__TextBugger: Generating Adversarial Text Against Real-world Applications.__ <br>
Deep Learning-based Text Understanding (DLTU) is the backbone technique behind various applications, including question answering, machine translation, and text classification. Despite its tremendous popularity, the security vulnerabilities of DLTU are still largely unknown, which is highly concerning given its increasing use in security-sensitive applications such as sentiment analysis and toxic content detection. In this paper, we show that DLTU is inherently vulnerable to adversarial text attacks, in which maliciously crafted texts trigger target DLTU systems and services to misbehave. Specifically, we present TextBugger, a general attack framework for generating adversarial texts. In contrast to prior works, TextBugger differs in significant ways: (i) effective -- it outperforms state-of-the-art attacks in terms of attack success rate; (ii) evasive -- it preserves the utility of benign text, with 94.9\% of the adversarial text correctly recognized by human readers; and (iii) efficient -- it generates adversarial text with computational complexity sub-linear to the text length. We empirically evaluate TextBugger on a set of real-world DLTU systems and services used for sentiment analysis and toxic content detection, demonstrating its effectiveness, evasiveness, and efficiency. For instance, TextBugger achieves 100\% success rate on the IMDB dataset based on Amazon AWS Comprehend within 4.61 seconds and preserves 97\% semantic similarity. We further discuss possible defense mechanisms to mitigate such attack and the adversary's potential countermeasures, which leads to promising directions for further research.



In [27]:
attack_recipe.value= 'TextBuggerLi2018'
tf.print(f'****Attack Recipe:{attack_recipe.value}*****')
tf.print(f'****Query size:{query_budget.value}*****')
tf.print(f'****Number of examples:{num_examples.value}*****')

****Attack Recipe:TextBuggerLi2018*****
****Query size:1000*****
****Number of examples:1000*****


#### BERT

In [ ]:
attack_model(bert, 
             dataset_for_attack,
             data_name.value,
             pretrained_weights.value,
             max_len.value,
             model_name.value,
             attack_recipe=attack_recipe.value,
             query_budget= query_budget.value,
             num_examples=num_examples.value)

textattack: Unknown if model of class <class 'keras.engine.functional.Functional'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path Result/IMDB/TextBuggerLi2018/DistilBERT_nexp1000_qb1000_2021-11-27_10:54.csv
  0%|          | 0/1000 [00:00<?, ?it/s]

Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  CompositeTransformation(
    (0): WordSwapRandomCharacterInsertion(
        (random_one):  True
      )
    (1): WordSwapRandomCharacterDeletion(
        (random_one):  True
      )
    (2): WordSwapNeighboringCharacterSwap(
        (random_one):  True
      )
    (3): WordSwapHomoglyphSwap
    (4): WordSwapEmbedding(
        (max_candidates):  5
        (embedding):  WordEmbedding
      )
    )
  (constraints): 
    (0): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8
        (window_size):  inf
        (skip_text_shorter_than_window):  False
        (compare_against_original):  True
      )
    (1): RepeatModification
    (2): StopwordModification
  (is_black_box):  True
) 



Using /tmp/tfhub_modules to cache modules.
Downloaded https://tfhub.dev/google/universal-sentence-encoder/4, Total size: 987.47MB
Downloaded TF-Hub Module 'https://tfhub.dev/google/universal-sentence-encoder/4'.
[Succeeded / Failed / Skipped / Total] 1 / 0 / 1 / 2:   0%|          | 2/1000 [00:20<2:53:39, 10.44s/it]

--------------------------------------------- Result 1 ---------------------------------------------
[[1 (73%)]] --> [[0 (58%)]]

this is perhaps the [[creepiest]] display of [[santa]] claus [[ever]] [[committed]] to any medium  whether it be a book  a [[picture]]  or a movie  santa looks [[like]] a perv [[looking]] down on the [[children]] and the twisted [[story]] of inging merlin in to help him defeat one of [[satan]] s minions  [[pitch]]  doesn t [[make]] [[things]] any [[better]]  it s laughable to [[say]] the least  with bad [[effects]]  [[even]] for   standards  if a [[kid]] were to [[watch]] this [[movie]]  he d have nightmares and never want santa to visit  they d be scarred for life  imagine the kid s in  a christmas story  when they start screaming after being put on santa s lap  that s how this would turn out if kid s see this movie 

this is perhaps the [[creеpiest]] display of [[saintly]] claus [[forever]] [[committeԁ]] to any medium  whether it be a book  a [[pictuⲅe]]  

[Succeeded / Failed / Skipped / Total] 2 / 0 / 1 / 3:   0%|          | 3/1000 [00:23<2:08:31,  7.73s/it]

...

--------------------------------------------- Result 842 ---------------------------------------------
[[0 (73%)]] --> [[1 (59%)]]

i saw this australian film about   years ago and have never forgotten it  the movie shows the horror of war in a way that hollywood usually glosses over  the relationship between the soldiers of the two warring countries is [[highlighted]] by the differences in culture and the ultimate [[knowledge]] that in the end we are all really not different on the inside  if you can find any type of copy of this buy or rent it  you won t be disappointed  just awed 

i saw this australian film about   years ago and have never forgotten it  the movie shows the horror of war in a way that hollywood usually glosses over  the relationship between the soldiers of the two warring countries is [[highlіghted]] by the differences in culture and the ultimate [[knwledge]] that in the end we are all really not different on the inside  if you can find any type of copy of this buy 

[Succeeded / Failed / Skipped / Total] 743 / 46 / 55 / 844:  84%|████████▍ | 844/1000 [29:28<05:26,  2.10s/it]

--------------------------------------------- Result 843 ---------------------------------------------
[[0 (73%)]] --> [[1 (61%)]]

normally i try to avoid barbie films  but this one was [[unmistakably]] awesome  kudos to the graphics and character voice overs  it all flowed well  this [[enchanting]] tale is a great spin off of others  but is well worth buying  i don t have kids  but the kids i babysit   including boys  find it [[intriguing]] and love the extra features on the dvd  i honestly don t know why this is rated so low  but for kids  especially your barbie lovin    year old will love this  its not straight forward and predictive like most movies are  this  childrens  film has excellent morals and shows teamwork  it has no swearing  bits of romance  if your old enough to figure it out  and beautifully written storyline  thats why i am giving it a ten out of ten 

normally i try to avoid barbie films  but this one was [[unmistakab]] [[ly]] awesome  kudos to the graphics and char

[Succeeded / Failed / Skipped / Total] 744 / 46 / 55 / 845:  84%|████████▍ | 845/1000 [29:29<05:24,  2.09s/it]

--------------------------------------------- Result 845 ---------------------------------------------
[[0 (73%)]] --> [[1 (57%)]]

chaplin enters the trenches of wwi in this [[spirited]] [[comedy]] that never belittles the horrors of war  the rain  the mud  the explosions   all these things are present but chaplin seems strangely oblivious to them all  he s in france for one thing  to fight the germans  something he does with unbelievable success     it almost seems like an extended ego trip for chaplin   a very [[funny]] one  at that   until the final minute when it rises to a new level of poignancy and everything makes sense     perhaps it s what all soldiers dream of before the go to war 

chaplin enters the trenches of wwi in this [[spiried]] [[comedian]] that never belittles the horrors of war  the rain  the mud  the explosions   all these things are present but chaplin seems strangely oblivious to them all  he s in france for one thing  to fight the germans  something he does wi

#### MT BERT

In [ ]:
attack_model(bert_teacher, 
             dataset_for_attack,
             data_name.value,
             pretrained_weights.value,
             max_len.value,
             'MT'+model_name.value,
             attack_recipe=attack_recipe.value,
             query_budget= query_budget.value,
             num_examples=num_examples.value)

### PWWS
__PWWSRen 2019 - Generating Natural Language Adversarial Examples through Probability Weighted Word Saliency. Shuhuai Ren, Yihe Deng, Kun He, Wanxiang Che__<br>
Based on the synonyms substitution strategy, they introduced a new word replacement order determined by both the word saliency and the classification probability, and propose a greedy algorithm called probability weighted word saliency (PWWS) for text adversarial attack.

In [ ]:
attack_recipe.value= 'PWWSRen2019'

# because of issue in PWWS attack provided by textattack I need to change the number of  queries = number of examples
# query_budget.value= num_examples.value

tf.print(f'****Attack Recipe:{attack_recipe.value}*****')
tf.print(f'****Query size:{query_budget.value}*****')
tf.print(f'****Number of examples:{num_examples.value}*****')



#### BERT

In [ ]:
attack_model(bert, 
             dataset_for_attack,
             data_name.value,
             pretrained_weights.value,
             max_len.value,
             model_name.value,
             attack_recipe=attack_recipe.value,
             query_budget= query_budget.value,
             num_examples=num_examples.value)

#### MT BERT

In [ ]:
attack_model(bert_teacher, 
             dataset_for_attack,
             data_name.value,
             pretrained_weights.value,
             max_len.value,
             'MT'+model_name.value,
             attack_recipe=attack_recipe.value,
             query_budget= query_budget.value,
             num_examples=num_examples.value)

### BAE
__BAEGarg2019-BAE (BAE: BERT-Based Adversarial Examples)__ <br>
BAE, a black box attack for generating adversarial examples using contextual perturbations from a BERT masked language model. BAE replaces and inserts tokens in the original text by masking a portion of the text and leveraging the BERT-MLM to generate alternatives for the masked tokens. Through automatic and human evaluations, we show that BAE performs a stronger attack, in addition to generating adversarial examples with improved grammaticality and semantic coherence as compared to prior work.


In [ ]:
attack_recipe.value= 'BAEGarg2019'
tf.print(f'****Attack Recipe:{attack_recipe.value}*****')
tf.print(f'****Query size:{query_budget.value}*****')
tf.print(f'****Number of examples:{num_examples.value}*****')

#### BERT

In [ ]:
attack_model(bert, 
             dataset_for_attack,
             data_name.value,
             pretrained_weights.value,
             max_len.value,
             model_name.value,
             attack_recipe=attack_recipe.value,
             query_budget= query_budget.value,
             num_examples=num_examples.value)

#### MT BERT

In [ ]:
attack_model(bert_teacher, 
             dataset_for_attack,
             data_name.value,
             pretrained_weights.value,
             max_len.value,
             'MT'+model_name.value,
             attack_recipe=attack_recipe.value,
             query_budget= query_budget.value,
             num_examples=num_examples.value)